In [1]:
import os
import math
import datetime

from tqdm import tqdm

import pandas as pd
import numpy as np

import tensorflow as tf
from tensorflow import keras

import bert
from bert import BertModelLayer
from bert.loader import StockBertConfig, map_stock_config_to_params, load_stock_weights
from bert.tokenization.bert_tokenization import FullTokenizer

In [2]:
bert_model_name="uncased_L-12_H-768_A-12"

bert_ckpt_dir = os.path.join("model/", bert_model_name)
bert_ckpt_file = os.path.join(bert_ckpt_dir, "bert_model.ckpt")
bert_config_file = os.path.join(bert_ckpt_dir, "bert_config.json")

In [3]:
tokenizer = FullTokenizer(vocab_file=os.path.join(bert_ckpt_dir, "vocab.txt"))

In [4]:
classes = ['service_availability_check',
            'billing_inquiry', 
            'order_cancellation',
              'address_verification',
                'user_authentication',
                  'account_information_update',
                    'call_divert', 
                    'customer_service_escalation',
                      'appointment_scheduling',
                        'order_status_inquiry',
                          'product_information_request',
                            'complaint_registration',
                              'call_disconnect',
                                'appointment_confirmation', 
                                'appointment_cancellation']


max_seq_len = 200

In [5]:
def create_model(max_seq_len, bert_ckpt_file):
  with tf.io.gfile.GFile(bert_config_file, "r") as reader:
      bc = StockBertConfig.from_json_string(reader.read())
      bert_params = map_stock_config_to_params(bc)
      bert_params.adapter_size = None
      bert = BertModelLayer.from_params(bert_params, name="bert")
  input_ids = keras.layers.Input(
    shape=(max_seq_len, ),
    dtype='int32',
    name="input_ids"
  )
  bert_output = bert(input_ids)
  print("bert shape", bert_output.shape)
  cls_out = keras.layers.Lambda(lambda seq: seq[:, 0, :])(bert_output)
  cls_out = keras.layers.Dropout(0.5)(cls_out)
  logits = keras.layers.Dense(units=768, activation="tanh")(cls_out)
  logits = keras.layers.Dropout(0.5)(logits)
  logits = keras.layers.Dense(
    units=len(classes),
    activation="softmax"
  )(logits)
  model = keras.Model(inputs=input_ids, outputs=logits)
  model.build(input_shape=(None, max_seq_len))
  load_stock_weights(bert, bert_ckpt_file)
  return model


In [ ]:
model = create_model(max_seq_len, bert_ckpt_file)

In [7]:
model.load_weights('bert_adv_synthetic_weights_v2(14).h5') 

In [17]:
# Run this if you change the max_seq_len
#model.save('bert_200_max_seq_len_model.h5') 
 

In [8]:
def intent_recognizer(sentences):
  pred_tokens = map(tokenizer.tokenize, sentences)
  pred_tokens = map(lambda tok: ["[CLS]"] + tok + ["[SEP]"], pred_tokens)
  pred_token_ids = list(map(tokenizer.convert_tokens_to_ids, pred_tokens))
  pred_token_ids = map(lambda tids: tids +[0]*(max_seq_len-len(tids)),pred_token_ids)
  pred_token_ids = np.array(list(pred_token_ids))
  predictions = model.predict(pred_token_ids).argmax(axis=-1)
  for text, label in zip(sentences, predictions):
    print("text:", text, "\nintent:", classes[label])
    print()

In [ ]:
sentences = ["While I’ve been speaking with you, I realized that my particular request might be better handled by someone with a more specialized focus. I believe there’s another team, maybe the one that deals with customer inquiries more closely, that would be better suited to help me. It seems like my issue falls outside the general scope, and I’d really appreciate being put in touch with the department or individual who is more equipped to provide the support I’m looking for. I’m thinking maybe the sales or technical support team could be more in line with what I need."]
intent_recognizer(sentences)